### Random Forest Classifier is an ensemble model that has proven to be fast and robust

This puts its speed closer to Ipaq8 rather than LSTM sluggishness

This is a proof of concept. No future data is ever used so we can turn it into exe ready.

In [1]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification
X, y = make_classification(n_samples=1000, n_features=4,
                           n_informative=2, n_redundant=0,
                           random_state=0, shuffle=False)
clf = RandomForestClassifier(criterion='entropy',max_depth=None, random_state=0)
clf.fit(X, y)

print(clf.predict_proba([[0, 0, 0, 0]]))
print(X.shape)
print(y.shape)

[[0.01 0.99]]
(1000, 4)
(1000,)


In [2]:
list_of_lists = []
with open('data\ecoli\Ecoli.txt') as f:
    for line in f:
        #inner_list = [elt.strip() for elt in line.split()]
        inner_list = list(line)
        list_of_lists.append(inner_list)
print(len(list_of_lists[0])) # About 4 MB
ecoli = list_of_lists[0]

import arithc as arith
import fqt, ppm
import contextlib, sys
import filecmp
from IPython.display import clear_output
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification

4638690


## Using Warm start

In [3]:
s = ecoli
char_list = [97, 103, 99, 116] # we can read this as we go
print(char_list)
update_period = len(s)

rf = RandomForestClassifier(n_estimators=10, warm_start = True, random_state=0)

legend = dict([(v, k) for k, v in enumerate(char_list)]) # map character to 0,1,2,3,4, etc.

temp_dict = {'a':97,'g': 103,'c': 99,'t': 116}
s = [temp_dict[i] for i in s]
#Train model
x = np.zeros((update_period-128, 128)) # 128 characters context
y = np.zeros((update_period-128))

print(len(s))
idx3 = 0
for idx2 in range(128,len(s)):
    train_seq = [legend[i] for i in s[idx2-128:idx2]] 
    train_target = legend[s[idx2]]
    x[idx3,:] = np.array(train_seq)
    y[idx3] = train_target
    idx3 += 1
predicted_onehot = []
for i in range(len(ecoli)//200000 - 1):
    print(i)
    rf.fit(x[200000*i:200000*(i+1)], y[200000*i:200000*(i+1)])
    rf.n_estimators += 10

    predicted_onehot += list(rf.predict_proba(x[200000*(i+1):200000*(i+2)]))
predicted_onehot += list(rf.predict_proba(x[200000*(len(ecoli)//200000):]))

[97, 103, 99, 116]
4638690
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21


In [4]:
rf.n_estimators


230

In [5]:
len(predicted_onehot)

4438562

In [7]:
np.save('temp', predicted_onehot)

In [5]:
predicted_onehot = np.load('temp.npy')

In [9]:

char_list = [97, 103, 99, 116]
def RF_Warmcompress(inp, bitout):
    initfreqs = fqt.FlatFrequencyTable(257)
    model = fqt.SimpleFrequencyTable(initfreqs) # For the first 200,000
    enc = arith.ArithmeticCoder(32)
    enc.start_encode(bitout) # New line!

    idx = 0
    while True:
        symbol = inp.read(1)
        if len(symbol) == 0:
                break

        idx += 1
        print(idx)
        ## Progress Evaluation ## only internal
        if idx % (len(ecoli)//10) == 0:
            print(str(10*idx//(len(ecoli)//10)) + ' percent done')
            clear_output(wait = True)
        if idx == 200129:
            initfreqs = fqt.FlatFrequencyTable(257)
            model = fqt.SimpleFrequencyTable(initfreqs) # reset the model
        if idx >= 200129:
            for val, prob in enumerate(predicted_onehot[idx-200129]):
                model.set(char_list[val], int(prob*100000)+1)
            
        t = model.get_total() ## New lines!
        l = model.get_low(symbol[0])
        h = model.get_high(symbol[0])
        enc.storeRegion(l,h,t) 
        
        if idx < 200129: # back up before LSTM model
            model.increment(symbol[0])
    t = model.get_total() ## New lines!
    l = model.get_low(256)
    h = model.get_high(256)
    enc.storeRegion(l,h,t)
    enc.finish_encode(bitout)  # New line!
inputfile, outputfile = 'data\ecoli\Ecoli.txt', 'data\ecoli\Ecoli_RF_warm.txt'

#Perform file compression
with open(inputfile, "rb") as inp, \
        contextlib.closing(arith.BitOutputStream(open(outputfile, "wb"))) as bitout:
    RF_Warmcompress(inp, bitout)

4174822
4174823
4174824
4174825
4174826
4174827
4174828
4174829
4174830
4174831
4174832
4174833
4174834
4174835
4174836
4174837
4174838
4174839
4174840
4174841
4174842
4174843
4174844
4174845
4174846
4174847
4174848
4174849
4174850
4174851
4174852
4174853
4174854
4174855
4174856
4174857
4174858
4174859
4174860
4174861
4174862
4174863
4174864
4174865
4174866
4174867
4174868
4174869
4174870
4174871
4174872
4174873
4174874
4174875
4174876
4174877
4174878
4174879
4174880
4174881
4174882
4174883
4174884
4174885
4174886
4174887
4174888
4174889
4174890
4174891
4174892
4174893
4174894
4174895
4174896
4174897
4174898
4174899
4174900
4174901
4174902
4174903
4174904
4174905
4174906
4174907
4174908
4174909
4174910
4174911
4174912
4174913
4174914
4174915
4174916
4174917
4174918
4174919
4174920
4174921
4174922
4174923
4174924
4174925
4174926
4174927
4174928
4174929
4174930
4174931
4174932
4174933
4174934
4174935
4174936
4174937
4174938
4174939
4174940
4174941
4174942
4174943
4174944
4174945
4174946


4176330
4176331
4176332
4176333
4176334
4176335
4176336
4176337
4176338
4176339
4176340
4176341
4176342
4176343
4176344
4176345
4176346
4176347
4176348
4176349
4176350
4176351
4176352
4176353
4176354
4176355
4176356
4176357
4176358
4176359
4176360
4176361
4176362
4176363
4176364
4176365
4176366
4176367
4176368
4176369
4176370
4176371
4176372
4176373
4176374
4176375
4176376
4176377
4176378
4176379
4176380
4176381
4176382
4176383
4176384
4176385
4176386
4176387
4176388
4176389
4176390
4176391
4176392
4176393
4176394
4176395
4176396
4176397
4176398
4176399
4176400
4176401
4176402
4176403
4176404
4176405
4176406
4176407
4176408
4176409
4176410
4176411
4176412
4176413
4176414
4176415
4176416
4176417
4176418
4176419
4176420
4176421
4176422
4176423
4176424
4176425
4176426
4176427
4176428
4176429
4176430
4176431
4176432
4176433
4176434
4176435
4176436
4176437
4176438
4176439
4176440
4176441
4176442
4176443
4176444
4176445
4176446
4176447
4176448
4176449
4176450
4176451
4176452
4176453
4176454


4177646
4177647
4177648
4177649
4177650
4177651
4177652
4177653
4177654
4177655
4177656
4177657
4177658
4177659
4177660
4177661
4177662
4177663
4177664
4177665
4177666
4177667
4177668
4177669
4177670
4177671
4177672
4177673
4177674
4177675
4177676
4177677
4177678
4177679
4177680
4177681
4177682
4177683
4177684
4177685
4177686
4177687
4177688
4177689
4177690
4177691
4177692
4177693
4177694
4177695
4177696
4177697
4177698
4177699
4177700
4177701
4177702
4177703
4177704
4177705
4177706
4177707
4177708
4177709
4177710
4177711
4177712
4177713
4177714
4177715
4177716
4177717
4177718
4177719
4177720
4177721
4177722
4177723
4177724
4177725
4177726
4177727
4177728
4177729
4177730
4177731
4177732
4177733
4177734
4177735
4177736
4177737
4177738
4177739
4177740
4177741
4177742
4177743
4177744
4177745
4177746
4177747
4177748
4177749
4177750
4177751
4177752
4177753
4177754
4177755
4177756
4177757
4177758
4177759
4177760
4177761
4177762
4177763
4177764
4177765
4177766
4177767
4177768
4177769
4177770


4179896
4179897
4179898
4179899
4179900
4179901
4179902
4179903
4179904
4179905
4179906
4179907
4179908
4179909
4179910
4179911
4179912
4179913
4179914
4179915
4179916
4179917
4179918
4179919
4179920
4179921
4179922
4179923
4179924
4179925
4179926
4179927
4179928
4179929
4179930
4179931
4179932
4179933
4179934
4179935
4179936
4179937
4179938
4179939
4179940
4179941
4179942
4179943
4179944
4179945
4179946
4179947
4179948
4179949
4179950
4179951
4179952
4179953
4179954
4179955
4179956
4179957
4179958
4179959
4179960
4179961
4179962
4179963
4179964
4179965
4179966
4179967
4179968
4179969
4179970
4179971
4179972
4179973
4179974
4179975
4179976
4179977
4179978
4179979
4179980
4179981
4179982
4179983
4179984
4179985
4179986
4179987
4179988
4179989
4179990
4179991
4179992
4179993
4179994
4179995
4179996
4179997
4179998
4179999
4180000
4180001
4180002
4180003
4180004
4180005
4180006
4180007
4180008
4180009
4180010
4180011
4180012
4180013
4180014
4180015
4180016
4180017
4180018
4180019
4180020


4182033
4182034
4182035
4182036
4182037
4182038
4182039
4182040
4182041
4182042
4182043
4182044
4182045
4182046
4182047
4182048
4182049
4182050
4182051
4182052
4182053
4182054
4182055
4182056
4182057
4182058
4182059
4182060
4182061
4182062
4182063
4182064
4182065
4182066
4182067
4182068
4182069
4182070
4182071
4182072
4182073
4182074
4182075
4182076
4182077
4182078
4182079
4182080
4182081
4182082
4182083
4182084
4182085
4182086
4182087
4182088
4182089
4182090
4182091
4182092
4182093
4182094
4182095
4182096
4182097
4182098
4182099
4182100
4182101
4182102
4182103
4182104
4182105
4182106
4182107
4182108
4182109
4182110
4182111
4182112
4182113
4182114
4182115
4182116
4182117
4182118
4182119
4182120
4182121
4182122
4182123
4182124
4182125
4182126
4182127
4182128
4182129
4182130
4182131
4182132
4182133
4182134
4182135
4182136
4182137
4182138
4182139
4182140
4182141
4182142
4182143
4182144
4182145
4182146
4182147
4182148
4182149
4182150
4182151
4182152
4182153
4182154
4182155
4182156
4182157


...

4629789
4629790
4629791
4629792
4629793
4629794
4629795
4629796
4629797
4629798
4629799
4629800
4629801
4629802
4629803
4629804
4629805
4629806
4629807
4629808
4629809
4629810
4629811
4629812
4629813
4629814
4629815
4629816
4629817
4629818
4629819
4629820
4629821
4629822
4629823
4629824
4629825
4629826
4629827
4629828
4629829
4629830
4629831
4629832
4629833
4629834
4629835
4629836
4629837
4629838
4629839
4629840
4629841
4629842
4629843
4629844
4629845
4629846
4629847
4629848
4629849
4629850
4629851
4629852
4629853
4629854
4629855
4629856
4629857
4629858
4629859
4629860
4629861
4629862
4629863
4629864
4629865
4629866
4629867
4629868
4629869
4629870
4629871
4629872
4629873
4629874
4629875
4629876
4629877
4629878
4629879
4629880
4629881
4629882
4629883
4629884
4629885
4629886
4629887
4629888
4629889
4629890
4629891
4629892
4629893
4629894
4629895
4629896
4629897
4629898
4629899
4629900
4629901
4629902
4629903
4629904
4629905
4629906
4629907
4629908
4629909
4629910
4629911
4629912
4629913


4631696
4631697
4631698
4631699
4631700
4631701
4631702
4631703
4631704
4631705
4631706
4631707
4631708
4631709
4631710
4631711
4631712
4631713
4631714
4631715
4631716
4631717
4631718
4631719
4631720
4631721
4631722
4631723
4631724
4631725
4631726
4631727
4631728
4631729
4631730
4631731
4631732
4631733
4631734
4631735
4631736
4631737
4631738
4631739
4631740
4631741
4631742
4631743
4631744
4631745
4631746
4631747
4631748
4631749
4631750
4631751
4631752
4631753
4631754
4631755
4631756
4631757
4631758
4631759
4631760
4631761
4631762
4631763
4631764
4631765
4631766
4631767
4631768
4631769
4631770
4631771
4631772
4631773
4631774
4631775
4631776
4631777
4631778
4631779
4631780
4631781
4631782
4631783
4631784
4631785
4631786
4631787
4631788
4631789
4631790
4631791
4631792
4631793
4631794
4631795
4631796
4631797
4631798
4631799
4631800
4631801
4631802
4631803
4631804
4631805
4631806
4631807
4631808
4631809
4631810
4631811
4631812
4631813
4631814
4631815
4631816
4631817
4631818
4631819
4631820


4633788
4633789
4633790
4633791
4633792
4633793
4633794
4633795
4633796
4633797
4633798
4633799
4633800
4633801
4633802
4633803
4633804
4633805
4633806
4633807
4633808
4633809
4633810
4633811
4633812
4633813
4633814
4633815
4633816
4633817
4633818
4633819
4633820
4633821
4633822
4633823
4633824
4633825
4633826
4633827
4633828
4633829
4633830
4633831
4633832
4633833
4633834
4633835
4633836
4633837
4633838
4633839
4633840
4633841
4633842
4633843
4633844
4633845
4633846
4633847
4633848
4633849
4633850
4633851
4633852
4633853
4633854
4633855
4633856
4633857
4633858
4633859
4633860
4633861
4633862
4633863
4633864
4633865
4633866
4633867
4633868
4633869
4633870
4633871
4633872
4633873
4633874
4633875
4633876
4633877
4633878
4633879
4633880
4633881
4633882
4633883
4633884
4633885
4633886
4633887
4633888
4633889
4633890
4633891
4633892
4633893
4633894
4633895
4633896
4633897
4633898
4633899
4633900
4633901
4633902
4633903
4633904
4633905
4633906
4633907
4633908
4633909
4633910
4633911
4633912


4635983
4635984
4635985
4635986
4635987
4635988
4635989
4635990
4635991
4635992
4635993
4635994
4635995
4635996
4635997
4635998
4635999
4636000
4636001
4636002
4636003
4636004
4636005
4636006
4636007
4636008
4636009
4636010
4636011
4636012
4636013
4636014
4636015
4636016
4636017
4636018
4636019
4636020
4636021
4636022
4636023
4636024
4636025
4636026
4636027
4636028
4636029
4636030
4636031
4636032
4636033
4636034
4636035
4636036
4636037
4636038
4636039
4636040
4636041
4636042
4636043
4636044
4636045
4636046
4636047
4636048
4636049
4636050
4636051
4636052
4636053
4636054
4636055
4636056
4636057
4636058
4636059
4636060
4636061
4636062
4636063
4636064
4636065
4636066
4636067
4636068
4636069
4636070
4636071
4636072
4636073
4636074
4636075
4636076
4636077
4636078
4636079
4636080
4636081
4636082
4636083
4636084
4636085
4636086
4636087
4636088
4636089
4636090
4636091
4636092
4636093
4636094
4636095
4636096
4636097
4636098
4636099
4636100
4636101
4636102
4636103
4636104
4636105
4636106
4636107


4638221
4638222
4638223
4638224
4638225
4638226
4638227
4638228
4638229
4638230
4638231
4638232
4638233
4638234
4638235
4638236
4638237
4638238
4638239
4638240
4638241
4638242
4638243
4638244
4638245
4638246
4638247
4638248
4638249
4638250
4638251
4638252
4638253
4638254
4638255
4638256
4638257
4638258
4638259
4638260
4638261
4638262
4638263
4638264
4638265
4638266
4638267
4638268
4638269
4638270
4638271
4638272
4638273
4638274
4638275
4638276
4638277
4638278
4638279
4638280
4638281
4638282
4638283
4638284
4638285
4638286
4638287
4638288
4638289
4638290
4638291
4638292
4638293
4638294
4638295
4638296
4638297
4638298
4638299
4638300
4638301
4638302
4638303
4638304
4638305
4638306
4638307
4638308
4638309
4638310
4638311
4638312
4638313
4638314
4638315
4638316
4638317
4638318
4638319
4638320
4638321
4638322
4638323
4638324
4638325
4638326
4638327
4638328
4638329
4638330
4638331
4638332
4638333
4638334
4638335
4638336
4638337
4638338
4638339
4638340
4638341
4638342
4638343
4638344
4638345


In [3]:
s = ecoli
char_list = [97, 103, 99, 116] # we can read this as we go
print(char_list)
update_period = len(s)

rf = RandomForestClassifier(n_estimators=100, warm_start = True, random_state=0)

legend = dict([(v, k) for k, v in enumerate(char_list)]) # map character to 0,1,2,3,4, etc.

temp_dict = {'a':97,'g': 103,'c': 99,'t': 116}
s = [temp_dict[i] for i in s]
#Train model
x = np.zeros((update_period-128, 128)) # 128 characters context
y = np.zeros((update_period-128))

print(len(s))
idx3 = 0
for idx2 in range(128,len(s)):
    train_seq = [legend[i] for i in s[idx2-128:idx2]] 
    train_target = legend[s[idx2]]
    x[idx3,:] = np.array(train_seq)
    y[idx3] = train_target
    idx3 += 1
predicted_onehot = []
for i in range(len(ecoli)//200000 - 1):
    print(i)
    rf.fit(x[200000*i:200000*(i+1)], y[200000*i:200000*(i+1)])
    rf.n_estimators += 5

    predicted_onehot += list(rf.predict_proba(x[200000*(i+1):200000*(i+2)]))
predicted_onehot += list(rf.predict_proba(x[200000*(len(ecoli)//200000):]))

[97, 103, 99, 116]
4638690
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21


In [4]:
np.save('temp2', predicted_onehot)

In [5]:
def RF_Warmcompress(inp, bitout):
    initfreqs = fqt.FlatFrequencyTable(257)
    model = fqt.SimpleFrequencyTable(initfreqs) # For the first 200,000
    enc = arith.ArithmeticCoder(32)
    enc.start_encode(bitout) # New line!

    idx = 0
    while True:
        symbol = inp.read(1)
        if len(symbol) == 0:
                break

        idx += 1
        ## Progress Evaluation ## only internal
        if idx % (len(ecoli)//10) == 0:
            print(str(10*idx//(len(ecoli)//10)) + ' percent done')
            clear_output(wait = True)
        if idx == 200129:
            initfreqs = fqt.FlatFrequencyTable(257)
            model = fqt.SimpleFrequencyTable(initfreqs) # reset the model
        if idx >= 200129:
            for val, prob in enumerate(predicted_onehot[idx-200129]):
                model.set(char_list[val], int(prob*100000)+1)
            
        t = model.get_total() ## New lines!
        l = model.get_low(symbol[0])
        h = model.get_high(symbol[0])
        enc.storeRegion(l,h,t) 
        
        if idx < 200129: # back up before LSTM model
            model.increment(symbol[0])
    t = model.get_total() ## New lines!
    l = model.get_low(256)
    h = model.get_high(256)
    enc.storeRegion(l,h,t)
    enc.finish_encode(bitout)  # New line!
inputfile, outputfile = 'data\ecoli\Ecoli.txt', 'data\ecoli\Ecoli_RF_warm2.txt'

#Perform file compression
with open(inputfile, "rb") as inp, \
        contextlib.closing(arith.BitOutputStream(open(outputfile, "wb"))) as bitout:
    RF_Warmcompress(inp, bitout)

100 percent done
